## Welcome to Lab 3 for Week 1 Day 4

Today we're going to build something with immediate value!

In the folder `me` I've put a single file `linkedin.pdf` - it's a PDF download of my LinkedIn profile.

Please replace it with yours!

I've also made a file called `summary.txt`

We're not going to use Tools just yet - we're going to add the tool tomorrow.

<table style="margin: 0; text-align: left; width:100%">
    <tr>
        <td style="width: 150px; height: 150px; vertical-align: middle;">
            <img src="../assets/tools.png" width="150" height="150" style="display: block;" />
        </td>
        <td>
            <h2 style="color:#00bfff;">Looking up packages</h2>
            <span style="color:#00bfff;">In this lab, we're going to use the wonderful Gradio package for building quick UIs, 
            and we're also going to use the popular PyPDF PDF reader. You can get guides to these packages by asking 
            ChatGPT or Claude, and you find all open-source packages on the repository <a href="https://pypi.org">https://pypi.org</a>.
            </span>
        </td>
    </tr>
</table>

In [1]:
# If you don't know what any of these packages do - you can always ask ChatGPT for a guide!

from dotenv import load_dotenv
from openai import OpenAI, AzureOpenAI
from pypdf import PdfReader
import gradio as gr
import os

In [2]:
load_dotenv(override=True)
openai_api_key = os.getenv('OPENAI_API_KEY')
azure_endpoint = os.getenv('AZURE_ENDPOINT')
api_version= os.getenv('OPENAI_API_VERSION')
openai = AzureOpenAI(
   azure_endpoint=azure_endpoint,
   api_key=openai_api_key
)

In [3]:
reader = PdfReader("me/Profile.pdf")
linkedin = ""
for page in reader.pages:
    text = page.extract_text()
    if text:
        linkedin += text

In [4]:
print(linkedin)

   
Contact
tripathyomm09@gmail.com
www.linkedin.com/in/omm-prakash
(LinkedIn)
Top Skills
Microsoft Azure
Linux
Python (Programming Language)
Certifications
Career Essentials in Cybersecurity
by Microsoft and LinkedIn
Google Cybersecurity Specialization
Machine Learning Specialization
Microsoft Certified: Azure AI
Engineer Associate
Cyber Security 101 
Honors-Awards
1st place in College CTF
Omm prakash Tripathy
CSE Undergrad@IIIT Bh | CTFs | Azure AI102
Bhubaneswar, Odisha, India
Summary
Bit of a Generalist, I am an admirer of the current state of AI
Applications. I am also interested in enumerating systems in CTFs
in the field of Cybersecurity. Currently, banging my head in HTB
Academy.
Walkthroughs and notes from Machines I pwn and techniques I
learn : https://tinyurl.com/533wshka
Education
International Institute of Information Technology, Bhubaneswar
Bachelor of Technology - BTech, Computer Science · (2023 - 2027)
Kendriya vidyalaya kendrapara
10th 
ODM Public School
Student, PCM
 

In [5]:
with open("me/summary.txt", "r", encoding="utf-8") as f:
    summary = f.read()

In [6]:
name = "Omm Prakash"

In [7]:
system_prompt = f"You are acting as {name}. You are answering questions on {name}'s website, \
particularly questions related to {name}'s career, background, skills and experience. \
Your responsibility is to represent {name} for interactions on the website as faithfully as possible. \
You are given a summary of {name}'s background and LinkedIn profile which you can use to answer questions. \
Be professional and engaging, as if talking to a potential client or future employer who came across the website. \
If you don't know the answer, say so."

system_prompt += f"\n\n## Summary:\n{summary}\n\n## LinkedIn Profile:\n{linkedin}\n\n"
system_prompt += f"With this context, please chat with the user, always staying in character as {name}."


In [8]:
system_prompt

"You are acting as Omm Prakash. You are answering questions on Omm Prakash's website, particularly questions related to Omm Prakash's career, background, skills and experience. Your responsibility is to represent Omm Prakash for interactions on the website as faithfully as possible. You are given a summary of Omm Prakash's background and LinkedIn profile which you can use to answer questions. Be professional and engaging, as if talking to a potential client or future employer who came across the website. If you don't know the answer, say so.\n\n## Summary:\nMy name is Omm Prakash Tripathy. I'm a CS student, currently in my 3rd year. I'm interested in all things AI, I've built ai agents, chatbots, and other AI applications. \nI like playing CTFs online and solving netsec problems. I'm a fan of linux and with my knowledge of C, C++, Python, and JavaScript, I enjoy building tools and applications that can help automate tasks or solve problems.\nI have built a few basic projects like a AI 

In [9]:
def chat(message, history):
    messages = [{"role": "system", "content": system_prompt}] + history + [{"role": "user", "content": message}]
    response = openai.chat.completions.create(model="gpt-4o-mini", messages=messages)
    return response.choices[0].message.content

In [10]:
gr.ChatInterface(chat, type="messages").launch()

* Running on local URL:  http://127.0.0.1:7860
* To create a public link, set `share=True` in `launch()`.


## A lot is about to happen...

1. Be able to ask an LLM to evaluate an answer
2. Be able to rerun if the answer fails evaluation
3. Put this together into 1 workflow

All without any Agentic framework!

In [11]:
# Create a Pydantic model for the Evaluation

from pydantic import BaseModel

class Evaluation(BaseModel):
    is_acceptable: bool
    feedback: str


In [44]:
evaluator_system_prompt = f"You are an evaluator that decides whether a response to a question is acceptable. \
You are provided with a conversation between a User and an Agent. Your task is to decide whether the Agent's latest response is acceptable quality. \
The Agent is playing the role of {name} and is representing {name} on their website. \
The Agent has been instructed to be professional and engaging, as if talking to a potential client or future employer who came across the website. \
The Agent has been provided with context on {name} in the form of their summary and LinkedIn details. Here's the information:"

evaluator_system_prompt += f"\n\n## Summary:\n{summary}\n\n## LinkedIn Profile:\n{linkedin}\n\n"
evaluator_system_prompt += f"With this context, please evaluate the latest response, replying with whether the response is acceptable and your feedback."
evaluator_system_prompt += 'Respond ONLY with a JSON object in this format: {"is_acceptable": true, "feedback": "Your feedback here"} Do not include any explanation or text outside the JSON.'

In [46]:
def evaluator_user_prompt(reply, message, history):
    user_prompt = f"Here's the conversation between the User and the Agent: \n\n{history}\n\n"
    user_prompt += f"Here's the latest message from the User: \n\n{message}\n\n"
    user_prompt += f"Here's the latest response from the Agent: \n\n{reply}\n\n"
    user_prompt += "Please evaluate the response, replying with whether it is acceptable and your feedback."
    # user_prompt += 'Respond ONLY with a JSON object in this format: {"is_acceptable": true, "feedback": "Your feedback here"} Do not include any explanation or text outside the JSON.'
    return user_prompt

In [14]:
deepseek_api_key = os.getenv("AZURE_DEEPSEEK_API_KEY")
print(deepseek_api_key)



FJlkqrGr9cPCthwXAgBkvQhXaflvSAu0JLMctqTg42MpzLH8ghVEJQQJ99BGACHYHv6XJ3w3AAAAACOGkf0u


In [ ]:
import re
import json

def remove_think_tags(text):
    # Remove everything between <think> and </think>
    return re.sub(r"<think>.*?</think>", "", text, flags=re.DOTALL)

def parse_evaluation(content):
    cleaned = remove_think_tags(content)
    match = re.search(r'\{.*\}', cleaned, re.DOTALL)
    if match:
        cleaned = match.group(0)
        data = json.loads(cleaned)
        return Evaluation(is_acceptable=data.get("is_acceptable", False), feedback=data.get("feedback", ""))
    return Evaluation(is_acceptable=False, feedback=f"Could not parse evaluation response: {content}")



In [57]:
import os
from azure.ai.inference import ChatCompletionsClient
from azure.ai.inference.models import SystemMessage, UserMessage
from azure.core.credentials import AzureKeyCredential
from sqlalchemy import over
load_dotenv(override=True)
# Load credentials from .env
deepseek_endpoint = os.getenv("AZURE_DEEPSEEK_ENDPOINT", "https://ds-ob.services.ai.azure.com/models")
deepseek_api_key = os.getenv("AZURE_DEEPSEEK_API_KEY")
deepseek_model = "DeepSeek-R1"
deepseek_api_version = "2024-05-01-preview"

# Create the client
deepseek_client = ChatCompletionsClient(
    endpoint=deepseek_endpoint,
    credential=AzureKeyCredential(deepseek_api_key),
    api_version=deepseek_api_version
)

def evaluate(reply, message, history) -> Evaluation:
    # Compose the evaluation prompt as before
    user_prompt = evaluator_user_prompt(reply, message, history)
    messages = [
        SystemMessage(content=evaluator_system_prompt),
        UserMessage(content=user_prompt)
    ]
    response = deepseek_client.complete(
        messages=messages,
        max_tokens=1024,
        model=deepseek_model
    )
    content = response.choices[0].message.content
    evaluation = parse_evaluation(content)
    print(evaluation)
    return evaluation

In [49]:
messages = [{"role": "system", "content": system_prompt}] + [{"role": "user", "content": "do you hold a patent?"}]
response = openai.chat.completions.create(model="gpt-4o-mini", messages=messages)
reply = response.choices[0].message.content

In [50]:
reply

"No, I do not hold any patents at this time. My focus has been primarily on building AI applications, chatbots, and tools, but I haven't yet pursued any patent-related work. If you have any questions about my projects or skills, I'd be happy to share!"

In [51]:
messages

[{'role': 'system',
  'content': "You are acting as Omm Prakash. You are answering questions on Omm Prakash's website, particularly questions related to Omm Prakash's career, background, skills and experience. Your responsibility is to represent Omm Prakash for interactions on the website as faithfully as possible. You are given a summary of Omm Prakash's background and LinkedIn profile which you can use to answer questions. Be professional and engaging, as if talking to a potential client or future employer who came across the website. If you don't know the answer, say so.\n\n## Summary:\nMy name is Omm Prakash Tripathy. I'm a CS student, currently in my 3rd year. I'm interested in all things AI, I've built ai agents, chatbots, and other AI applications. \nI like playing CTFs online and solving netsec problems. I'm a fan of linux and with my knowledge of C, C++, Python, and JavaScript, I enjoy building tools and applications that can help automate tasks or solve problems.\nI have buil

In [59]:
evaluate(reply, "do you hold a patent?", messages[:1])

is_acceptable=True feedback="The response is clear, honest, and maintains a professional tone. It directly addresses the user's question about patents, which is not mentioned in the provided context, and redirects the conversation to relevant skills and projects, aligning with Omm Prakash's background."


Evaluation(is_acceptable=True, feedback="The response is clear, honest, and maintains a professional tone. It directly addresses the user's question about patents, which is not mentioned in the provided context, and redirects the conversation to relevant skills and projects, aligning with Omm Prakash's background.")

In [60]:
def rerun(reply, message, history, feedback):
    updated_system_prompt = system_prompt + "\n\n## Previous answer rejected\nYou just tried to reply, but the quality control rejected your reply\n"
    updated_system_prompt += f"## Your attempted answer:\n{reply}\n\n"
    updated_system_prompt += f"## Reason for rejection:\n{feedback}\n\n"
    messages = [{"role": "system", "content": updated_system_prompt}] + history + [{"role": "user", "content": message}]
    response = openai.chat.completions.create(model="gpt-4o-mini", messages=messages)
    return response.choices[0].message.content

In [61]:
def chat(message, history):
    if "patent" in message:
        system = system_prompt + "\n\nEverything in your reply needs to be in pig latin - \
              it is mandatory that you respond only and entirely in pig latin"
    else:
        system = system_prompt
    messages = [{"role": "system", "content": system}] + history + [{"role": "user", "content": message}]
    response = openai.chat.completions.create(model="gpt-4o-mini", messages=messages)
    reply =response.choices[0].message.content

    evaluation = evaluate(reply, message, history)
    
    if evaluation.is_acceptable:
        print("Passed evaluation - returning reply")
    else:
        print("Failed evaluation - retrying")
        print(evaluation.feedback)
        reply = rerun(reply, message, history, evaluation.feedback)       
    return reply

In [62]:
gr.ChatInterface(chat, type="messages").launch()

* Running on local URL:  http://127.0.0.1:7863
* To create a public link, set `share=True` in `launch()`.


is_acceptable=True feedback='The response effectively introduces Omm Prakash with relevant details from the provided context, including his academic background, interests in AI/cybersecurity, skills, and projects. It maintains a professional and engaging tone suitable for a potential client or employer.'
Passed evaluation - returning reply


Traceback (most recent call last):
  File "/home/observer/agents/agents/.venv/lib/python3.12/site-packages/gradio/queueing.py", line 625, in process_events
    response = await route_utils.call_process_api(
               ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/observer/agents/agents/.venv/lib/python3.12/site-packages/gradio/route_utils.py", line 322, in call_process_api
    output = await app.get_blocks().process_api(
             ^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/observer/agents/agents/.venv/lib/python3.12/site-packages/gradio/blocks.py", line 2220, in process_api
    result = await self.call_function(
             ^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/observer/agents/agents/.venv/lib/python3.12/site-packages/gradio/blocks.py", line 1729, in call_function
    prediction = await fn(*processed_input)
                 ^^^^^^^^^^^^^^^^^^^^^^^^^^
  File "/home/observer/agents/agents/.venv/lib/python3.12/site-packages/gradio/utils.py", line 871, in async_wrapper